### Camada Silver: Refinamento dos dados brutos da camada Bronze

A Camada Silver da arquitetura Medallion é dedicada ao refinamento dos dados brutos provenientes da Bronze. Nessa etapa, são realizadas transformações, desnormalizações e correções de inconsistências, preparando os dados para análises mais detalhadas e confiáveis. O particionamento por critérios como ano e mês desempenha um papel fundamental na organização e no desempenho do Data Lake, permitindo consultas mais eficientes. Essa abordagem reduz o número de arquivos escaneados em consultas filtradas por períodos específicos, acelerando a recuperação de informações e melhorando a performance, especialmente em grandes volumes de dados.

A limpeza de dados é essencial para assegurar a qualidade e a precisão das informações. Essa fase engloba tarefas como a remoção de duplicidades, correção de erros, padronização de formatos e enriquecimento dos dados com informações adicionais. Essas ações não apenas garantem a consistência dos dados, mas também aumentam sua utilidade para análises e tomadas de decisão.

O código a seguir demonstra como processar os dados da camada Bronze, aplicando configurações otimizadas do Spark, e como armazená-los na camada Silver para suportar análises avançadas de forma eficiente.

In [0]:
# Importar as bibliotecas necessárias
from pyspark.sql import SparkSession
from pyspark.sql.functions import *
from pyspark.sql.types import *

# Iniciar a SparkSession com configurações otimizadas
spark = SparkSession.builder \
    .appName("Transformação Data Silver") \
    .config("spark.sql.shuffle.partitions", "200") \
    .config("spark.sql.files.maxPartitionBytes", "128MB") \
    .config("spark.sql.parquet.compression.codec", "snappy") \
    .config("spark.sql.adaptive.enabled", "true") \
    .getOrCreate()

# appName: Nome da aplicação para identificação no cluster
# "spark.sql.shuffle.partitions": Define o número de partições de shuffle para melhorar o paralelismo
# "spark.sql.files.maxPartitionBytes": Limita o tamanho das partições para evitar arquivos pequenos
# "spark.sql.parquet.compression.codec": Usa compressão Snappy para otimizar leitura/escrita
# "spark.sql.adaptive.enabled": Ativa otimizações adaptativas no Spark


# Definir os caminhos de armazenamento no Data Lake
bronze_path = "/mnt/lhdw/bronze/vendas"  # Caminho da camada Bronze com dados brutos
silver_path = "/mnt/lhdw/silver/vendas"  # Caminho da camada Silver para salvar os dados refinados

# Leitura dos dados da camada Bronze
df_bronze = spark.read.format("parquet").load(bronze_path) # Lê os dados da Bronze no formato Parquet

# Realizar transformações necessárias para limpar, formatar e organizar os dados do DataFrame df_bronze
df_silver = df_bronze.withColumn("Data", to_date(col("Data"), "yyyy-MM-dd")) \
                .withColumn("Email", lower(expr("regexp_replace(split(EmailNome, ':')[0], '[()]', '')"))) \
                .withColumn("Nome", expr("split(split(EmailNome, ':')[1], ', ')")) \
                .withColumn("Nome", expr("concat(Nome[1], ' ', Nome[0])")) \
                .withColumn("Cidade", expr("split(Cidade, ',')[0]")) \
                .withColumn("PrecoUnitario", format_number(col("PrecoUnitario"), 2)) \
                .withColumn("CustoUnitario", format_number(col("CustoUnitario"), 2)) \
                .withColumn("TotalVendas", format_number(col("PrecoUnitario") * col("Unidades"),2))\
                .drop("EmailNome")\
                .drop("IdCampanha")   

# Exibindo o DataFrame resultante com as transformações aplicadas
display(df_silver)

# Adicionar colunas "Ano" e "Mes" ao DataFrame para particionamento, extraídas da coluna "Data"
# Explicação de cada linha do código abaixo:
#   Extrai o ano da coluna "Data" e cria a coluna "Ano"
#   Extrai o mês da coluna "Data" e cria a coluna "Mes"
#   Define um limite de 50.000 registros por arquivo para otimização
#   Particiona os dados pelas colunas "Ano" e "Mes" para facilitar consultas baseadas em tempo
#   Define o formato de saída como Parquet, eficiente para armazenamento e consultas
#   Sobrescreve os dados existentes no caminho especificado, caso existam
#   Salva os dados processados no caminho da Camada Silver
df_silver.withColumn("Ano", year("Data")) \
         .withColumn("Mes", month("Data")) \
         .write.option("maxRecordsPerFile", 50000) \
         .partitionBy("Ano", "Mes") \
         .format("parquet") \
         .mode("overwrite") \
         .save(silver_path)

# Contar e exibir o número total de registros no DataFrame
df_silver.count()


IDProduto Data IDCliente Unidades Produto Categoria Segmento IDFabricante Fabricante CustoUnitario PrecoUnitario CodigoPostal Cidade Estado Regiao Distrito Pais filename Ano Mes Email Nome TotalVendas 433 2012-06-08 248728 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 25275 Sandyville WV East District #15 USA dados_2012.csv 2012 6 hall.goff@xyza.com Hall Goff 100.79 433 2012-06-22 118344 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 8087 Tuckerton NJ East District #04 USA dados_2012.csv 2012 6 stewart.bullock@xyza.com Stewart Bullock 100.79 433 2012-06-17 239188 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 8802 Asbury NJ East District #03 USA dados_2012.csv 2012 6 wallace.medina@xyza.com Wallace Medina 100.79 433 2012-06-03 172295 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 8533 New Egypt NJ East District #04 USA dados_2012.csv 2012 6 willa.downs@xyza.com Willa Downs 100.79 433 2012-06-29 154989 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 41017 Ft Mitchell KY East District #16 USA dados_2012.csv 2012 6 timothy.simmons@xyza.com Timothy Simmons 100.79 433 2012-06-09 181005 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 20872 Damascus MD East District #05 USA dados_2012.csv 2012 6 diana.tran@xyza.com Diana Tran 100.79 433 2012-06-29 131786 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 31008 Byron GA East District #09 USA dados_2012.csv 2012 6 tyler.yang@xyza.com Tyler Yang 100.79 433 2012-06-15 54787 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 30060 Marietta GA East District #09 USA dados_2012.csv 2012 6 price.guzman@xyza.com Price Guzman 100.79 433 2012-06-15 54788 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 30060 Marietta GA East District #09 USA dados_2012.csv 2012 6 brock.gordon@xyza.com Brock Gordon 100.79 433 2012-06-13 162176 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 31316 Ludowici GA East District #11 USA dados_2012.csv 2012 6 jonas.wong@xyza.com Jonas Wong 100.79 433 2012-06-10 41022 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 23452 Virginia Beach VA East District #07 USA dados_2012.csv 2012 6 mckenzie.leblanc@xyza.com McKenzie Leblanc 100.79 433 2012-06-14 277764 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 23356 Greenbackville VA East District #07 USA dados_2012.csv 2012 6 samantha.gallegos@xyza.com Samantha Gallegos 100.79 433 2012-06-10 107537 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 20151 Chantilly VA East District #07 USA dados_2012.csv 2012 6 karyn.higgins@xyza.com Karyn Higgins 100.79 433 2012-06-10 107538 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 20151 Chantilly VA East District #07 USA dados_2012.csv 2012 6 isaiah.roman@xyza.com Isaiah Roman 100.79 433 2012-06-20 214524 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 20191 Reston VA East District #07 USA dados_2012.csv 2012 6 gretchen.kaufman@xyza.com Gretchen Kaufman 100.79 433 2012-06-20 101169 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 23692 Yorktown VA East District #07 USA dados_2012.csv 2012 6 callie.alexander@xyza.com Callie Alexander 100.79 433 2012-06-09 214012 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 25413 Bunker Hill WV East District #07 USA dados_2012.csv 2012 6 shellie.gibson@xyza.com Shellie Gibson 100.79 433 2012-06-28 228078 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 46148 Knightstown IN East District #17 USA dados_2012.csv 2012 6 kirk.oconnor@xyza.com Kirk Oconnor 100.79 433 2012-06-17 138402 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 46001 Alexandria IN East District #17 USA dados_2012.csv 2012 6 casey.ramirez@xyza.com Casey Ramirez 100.79 433 2012-06-30 145624 1 Maximus UM-38 Urban Moderation 7 VanArsdel 73.58 100.79 46582 Warsaw IN East District #17 USA dados_2012.csv 2012 6 rahim.dunlap@xyza.com Rahim Dunlap 100.79 433 2012-06-07 204903 1 Maximus UM-38 Urban Moderation 7 VanArsdel 

Out[1]: 116895

### Limpar a Memória

In [0]:
# Importa o módulo "gc" (Garbage Collector) do Python para gerenciar a coleta de objetos não utilizados na memória.
import gc

# Força a execução imediata do coletor de lixo.
# Isso limpa objetos Python que não estão mais sendo referenciados, liberando memória.
gc.collect()

# Remove explicitamente a variável "df_bronze" da memória.
# Isso é útil para liberar espaço, especialmente ao trabalhar com grandes DataFrames que não são mais necessários.
del df_bronze

# Remove explicitamente a variável "df_silver" da memória.
# Boa prática para liberar memória em ambientes com recursos limitados ou grandes volumes de dados.
del df_silver